<div style="background-color: #d6ccc2; color: black; ">
    <h3 align="center"> </h3>
    <h1 align="center">Analyzing Airline Ticket Data from Expedia</h1>
    <h3 align="center">Uncovering Insights from 23 Million Rows of One-Way Flight Information</h3>
    <h3 align="center"> </h3>

</div>
<div style="background-color: #edede9; color: black; ">
    <h3 align="center"> </h3>
    <p style="font-size: 16px; text-align: justify; font-weight: 500; margin: 15px;">Here, we analyzed data from the Expedia website, which includes information on one-way airline tickets. This dataset covers a specific period of online ticket purchases and consists of 23 million rows. Each row represents a flight ticket that was available for purchase on the Expedia website on a particular date.</p>
    <h3 align="center"> </h3>
</div>

# 1. Exploring and Visualizing Expedia Flight Data

In [1]:
!pip install -q duckdb

import numpy as np 
import pandas as pd 
import duckdb as db
import plotly.express as px
import re
import statsmodels.api as sm



import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

/kaggle/input/expedia-2022-06-to-2023-01/expedia_2022-06_to_2023-01.parquet


In [2]:
db.sql('''
CREATE OR REPLACE TABLE expedia AS 
SELECT * FROM '/kaggle/input/expedia-2022-06-to-2023-01/expedia_2022-06_to_2023-01.parquet'; ''')

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

## 1.1 Ticket Pricing

In [3]:
df1 = db.sql('''SELECT legId, totalFare, flightDate, isBasicEconomy
                FROM expedia;''').to_df()

#Distribution of Ticket Prices
bins = [0, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000, np.inf]
labels = ['$0-100', '$100-200', '$200-300', '$300-400', '$400-500', 
          '$500-600', '$600-700', '$700-800', '$800-900', '$900-1000', '$1000+']
df1['price_bin'] = pd.cut(df1['totalFare'], bins=bins, labels=labels, right=False)
price_distribution = df1['price_bin'].value_counts().sort_index().reset_index()

fig1 = px.bar(price_distribution, x='price_bin', y='count',
             title='Distribution of Ticket Prices',
             labels={'price_bin': 'Price Range (USD)', 'count': 'Number of Tickets'},
             color_discrete_sequence=['#cb997e'])

fig1.update_layout(
    plot_bgcolor='#e9ecef',
    xaxis_title='Price Range (USD)',
    yaxis_title='Number of Tickets',
    title=dict(x=0.5)
)

#isBasicEconomy
economy_distribution = df1['isBasicEconomy'].value_counts(normalize=True).reset_index()

fig2 = px.pie(economy_distribution, 
             values='proportion', 
             names='isBasicEconomy', 
             title='Percentage of Economy vs Non-Economy Tickets',
             labels={'isBasicEconomy': 'Ticket Type', 'proportion':'percentage'},
             color_discrete_sequence=['#6c584c', '#adc178'])
fig2.update_traces(textposition='inside', textinfo='percent+label')
fig2.update_layout(title=dict(x=0.5))


#Price Fluctuations Over Time
df1M = df1[['legId', 'flightDate', 'totalFare']].groupby(['legId', 'flightDate']).mean().reset_index()
df2 = df1M[['flightDate', 'totalFare']].groupby('flightDate').mean().reset_index()
fig3 = px.line(df2, x='flightDate', y='totalFare',
              title='Price Fluctuations Over Time',
              labels={'flightDate': 'Date', 'totalFare': 'Average Fare (USD)'})
fig3.update_traces(line=dict(color='#6c584c'))  # Change the color of the line
fig3.update_layout(
    plot_bgcolor='#e9ecef',
    title=dict(x=0.5)
)

#Average Ticket Price by Day of the Week
df3 = df1M.loc[:, ['flightDate', 'totalFare']]
df3['flightDate'] = pd.to_datetime(df3['flightDate'])

df3['flight_weekday'] = df3['flightDate'].apply(lambda x:x.weekday())
df3['flight_day_name'] = df3['flightDate'].apply(lambda x:x.day_name())
df3 = df3.groupby(['flight_weekday' , 'flight_day_name']).mean().reset_index()

fig4 = px.line(df3, x='flight_day_name', y='totalFare',
              title='Average Ticket Price by Day of the Week',
              labels={'flight_day_name': 'Day of the Week', 'totalFare': 'Average Fare (USD)'})
fig4.update_traces(line=dict(color='#6c584c'))  # Change the color of the line
fig4.update_layout(
    plot_bgcolor='#e9ecef',
    title=dict(x=0.5)
)

fig1.show()
fig2.show()
fig3.show()
fig4.show()

## 1.2 Number of Flights

<div style="background-color: #edede9; color: black; width: 50%; float: left; box-sizing: border-box; padding: 20px;">
    <h3 align="center"></h3>
    <p style="font-size: 16px; text-align: justify; font-weight: 500;">A lot of the tickets in this dataset were for flights with stops. I broke these up into non-stop flights, since each segment might have already been listed separately or as part of another flight with stops. After that, I checked for duplicate flights that had the same origin, destination, start time, and end time to make sure we didn’t count the same flight more than once. This helped ensure we only counted unique flights. After splitting the data and removing duplicates, we ended up with 100 rows of data.</p>
    <h3 align="center"></h3>
</div>

<div style="width: 50%; height: auto; float: right; box-sizing: border-box; padding: 20px; display: flex; justify-content: center; align-items: center;" >
    <img src="https://cdn-icons-png.flaticon.com/256/12114/12114821.png" alt="Image" style="max-width: 50%; height: 90%; margin: 40px;">
</div>


In [4]:
df4 = db.sql('''select distinct legId,
               segmentsDepartureAirportCode,destinationAirport,
               segmentsDepartureTimeRaw, segmentsArrivalTimeRaw, travelDuration
               from expedia''').to_df()
df4['path'] = df4['segmentsDepartureAirportCode'] + '||' + df4['destinationAirport']
data = df4[['legId', 'path', 'segmentsDepartureTimeRaw', 'segmentsArrivalTimeRaw']]
data.columns = ['index','path', 'departure', 'arrival']

def transform_flight_data(df):
    df = df.fillna("")
    def transform_row(row):
        
        paths = row['path'].split('||')
        arrivals = row['arrival'].split('||')
        departures = row['departure'].split('||')
        
        new_rows = []
        for i in range(len(paths) - 1):
            new_row = {
                'index': row['index'],
                'origin': paths[i],
                'destination': paths[i + 1],
                'departure': departures[i],
                'arrival': arrivals[i], 
            }
            new_rows.append(new_row)

        return new_rows
             
    transformed_data = []
    for _, row in df.iterrows():
        transformed_data.extend(transform_row(row))

    transformed_df = pd.DataFrame(transformed_data)

    return transformed_df

result = transform_flight_data(data)
unique_data = result.drop_duplicates(['origin','destination', 'departure', 'arrival']).reset_index(drop=True)

unique_data['departure'] = pd.to_datetime(unique_data['departure'], utc=True)
unique_data['flightDate'] = unique_data['departure'].dt.date
unique_data['flightDate'] = pd.to_datetime(unique_data['flightDate'])

print(unique_data.shape)
unique_data.head()

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

(537783, 6)


index origin destination  \
0  7a384f9b6a78a8ac3a5cd5444c8b2858    BOS         SEA   
1  7a384f9b6a78a8ac3a5cd5444c8b2858    SEA         SFO   
2  520332957f58509cb753e30c61ac9f2b    BOS         JFK   
3  520332957f58509cb753e30c61ac9f2b    JFK         SFO   
4  a288c560344067732f2ecd4e87eca7f3    BOS         JFK   

                  departure                        arrival flightDate  
0 2022-06-03 23:05:00+00:00  2022-06-03T22:20:00.000-07:00 2022-06-03  
1 2022-06-04 13:00:00+00:00  2022-06-04T08:12:00.000-07:00 2022-06-04  
2 2022-06-03 10:05:00+00:00  2022-06-03T07:25:00.000-04:00 2022-06-03  
3 2022-06-03 13:30:00+00:00  2022-06-03T12:55:00.000-07:00 2022-06-03  
4 2022-06-03 13:40:00+00:00  2022-06-03T11:02:00.000-04:00 2022-06-03

In [56]:
unique_data['flight_weekday'] = unique_data['flightDate'].apply(lambda x:x.weekday())
unique_data['flight_day_name'] = unique_data['flightDate'].apply(lambda x:x.strftime('%A'))

number_of_flights = unique_data[['flightDate']].value_counts().reset_index().sort_values('flightDate')[:-4]
flights_per_day = unique_data[['flight_weekday', 'flight_day_name']].value_counts().reset_index().sort_values('flight_weekday')
flights_per_day

# Number of Flights
fig1 = px.line(number_of_flights, x='flightDate', y='count',
              title='Number of Flights',
              labels={'flight_day_name': 'date', 'count': 'Number of Flights'})

fig1.update_traces(line=dict(color='#432818'))  # Change the color of the line

fig1.update_layout(
    plot_bgcolor='#e9ecef',
    paper_bgcolor='white',
    title=dict(x=0.5))

# Number of Flights Per Week Day
fig2 = px.line(flights_per_day, x='flight_day_name', y='count',
              title='Number of Flights per Weekday',
              labels={'flight_day_name': 'Weekday', 'count': 'Number of Flights'})

fig2.update_traces(line=dict(color='#432818'))  # Change the color of the line

fig2.update_layout(
    plot_bgcolor='#e9ecef',
    paper_bgcolor='white',
    title=dict(x=0.5))

fig1.show()
fig2.show()

## 1.3 Flight Durations 

In [58]:
def duration_to_minutes(duration):
    days = re.search(r'(\d+)D', duration)
    hours = re.search(r'(\d+)H', duration)
    minutes = re.search(r'(\d+)M', duration)
    
    total_minutes = 0
    if days:
        total_minutes += int(days.group(1)) * 24 * 60
    if hours:
        total_minutes += int(hours.group(1)) * 60
    if minutes:
        total_minutes += int(minutes.group(1))
    
    return total_minutes

df4['travelDurationMinutes'] = df4['travelDuration'].apply(duration_to_minutes)

fig = px.histogram(df4, 
                   x='travelDurationMinutes',
                   nbins=30, 
                   title='Distribution of Flight Durations',
                   labels={'travelDurationMinutes': 'Flight Duration (minutes)'},
                   color_discrete_sequence=['#708d81'])

fig.update_layout(
    plot_bgcolor='#e9ecef',
        title=dict(x=0.5)
)
fig.show()


# 2. QUESTION: What factors affect flight ticket prices?

In [5]:
q2 = db.sql('''
WITH MeanFares AS (
    SELECT
        legId,
        AVG(totalFare) AS mean_of_fare
    FROM
        expedia
    WHERE
        isNonStop = True
    GROUP BY
        legId
)
SELECT
    e.legId,
    e.flightDate,
    e.segmentsArrivalAirportCode,
    e.segmentsDepartureAirportCode,
    e.isBasicEconomy,
    mf.mean_of_fare,
    e.totalTravelDistance,
    e.segmentsDepartureTimeRaw,
    e.segmentsArrivalTimeRaw,
    e.segmentsAirlineName,
    e.segmentsDurationInSeconds,
    e.segmentsCabinCode
FROM
    expedia e
JOIN
    MeanFares mf
ON
    e.legId = mf.legId
WHERE
    e.rowid = (
        SELECT MAX(sub.rowid)
        FROM expedia sub
        WHERE sub.legId = e.legId
    )
                ''').to_df()

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

In [6]:
q2.columns = ['legId', 'flightDate', 'destinationAirport',
       'startingAirport', 'isBasicEconomy', 'mean_of_fare',
       'totalTravelDistance', 'departureTimeRaw','arrivalTimeRaw', 
       'airlineName','durationInSeconds', 'cabinCode']
q2.head()

legId  flightDate destinationAirport  \
0  34c11aca6673ed3146fcfe62b310aea2  2022-06-01                BOS   
1  13015c2cd873368177694a80a0d3082a  2022-06-01                JFK   
2  989c8feb66721a100faaa3a0e1d81e88  2022-06-01                JFK   
3  4fc6c92f2d0dbc673bb7eb776a65206b  2022-06-01                PHL   
4  373d455da68ce920c3440d03aea16f73  2022-06-01                PHL   

  startingAirport  isBasicEconomy  mean_of_fare  totalTravelDistance  \
0             ATL           False    254.600000                947.0   
1             BOS           False     63.600000                185.0   
2             BOS           False    153.600000                185.0   
3             BOS           False     73.885714                280.0   
4             BOS           False     92.206000                280.0   

                departureTimeRaw                 arrivalTimeRaw  \
0  2022-06-01T17:11:00.000-04:00  2022-06-01T19:56:00.000-04:00   
1  2022-06-01T18:35:00.000-04:00  2022-06-01T19:59:00.000-04:00   
2  2022-06-01T08:00:00.000-04:00  2022-06-01T09:16:00.000-04:00   
3  2022-06-01T06:30:00.000-04:00  2022-06-01T08:13:00.000-04:00   
4  2022-06-01T15:45:00.000-04:00  2022-06-01T17:28:00.000-04:00   

       airlineName durationInSeconds cabinCode  
0  JetBlue Airways              9900     coach  
1  JetBlue Airways              5040     coach  
2  JetBlue Airways              4560     coach  
3            Delta              6180     coach  
4  JetBlue Airways              6180     coach

In [7]:
q2['flightDate'] = pd.to_datetime(q2['flightDate'])
q2['departureTimeRaw'] = pd.to_datetime(q2['departureTimeRaw'], utc=True)
q2['arrivalTimeRaw'] = pd.to_datetime(q2['arrivalTimeRaw'], utc=True)
q2['flight_day_name'] = q2['flightDate'].apply(lambda x:x.strftime('%A'))
q2['totalTravelDistance'].fillna(q2['totalTravelDistance'].mean(), inplace=True)
q2['departureTimeRaw'] = pd.to_datetime(q2['departureTimeRaw'])
q2['arrivalTimeRaw'] = pd.to_datetime(q2['arrivalTimeRaw'])
q2['flight_duration_hours'] = (q2['arrivalTimeRaw'] - q2['departureTimeRaw']).dt.total_seconds() / 3600
df = q2.drop(columns=['legId', 'flightDate', 'departureTimeRaw', 'arrivalTimeRaw', 'durationInSeconds'])
df

/tmp/ipykernel_36/970120367.py:5: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.





destinationAirport startingAirport  isBasicEconomy  mean_of_fare  \
0                     BOS             ATL           False    254.600000   
1                     JFK             BOS           False     63.600000   
2                     JFK             BOS           False    153.600000   
3                     PHL             BOS           False     73.885714   
4                     PHL             BOS           False     92.206000   
...                   ...             ...             ...           ...   
218795                DTW             MIA           False    123.256667   
218796                JFK             LAX           False    307.350000   
218797                JFK             BOS           False    221.933333   
218798                DTW             ORD           False    173.602500   
218799                LAX             DTW           False    181.090000   

        totalTravelDistance        airlineName cabinCode flight_day_name  \
0                947.000000    JetBlue Airways     coach       Wednesday   
1                185.000000    JetBlue Airways     coach       Wednesday   
2                185.000000    JetBlue Airways     coach       Wednesday   
3                280.000000              Delta     coach       Wednesday   
4                280.000000    JetBlue Airways     coach       Wednesday   
...                     ...                ...       ...             ...   
218795          1279.692868    Spirit Airlines     coach          Monday   
218796          2467.000000  American Airlines     coach       Wednesday   
218797           186.000000    JetBlue Airways     coach        Thursday   
218798           240.000000              Delta     coach         Tuesday   
218799          1279.692868    Spirit Airlines     coach          Sunday   

        flight_duration_hours  
0                    2.750000  
1                    1.400000  
2                    1.266667  
3                    1.716667  
4                    1.716667  
...                       ...  
218795               3.083333  
218796               5.250000  
218797               1.416667  
218798               1.400000  
218799               5.116667  

[218800 rows x 9 columns]

In [8]:
model = sm.OLS.from_formula("mean_of_fare ~ isBasicEconomy + totalTravelDistance + flight_duration_hours + C(cabinCode) ", data=df).fit()
print(model.summary())

                            OLS Regression Results                            
Dep. Variable:           mean_of_fare   R-squared:                       0.698
Model:                            OLS   Adj. R-squared:                  0.698
Method:                 Least Squares   F-statistic:                 8.410e+04
Date:                Mon, 07 Oct 2024   Prob (F-statistic):               0.00
Time:                        20:34:11   Log-Likelihood:            -1.4566e+06
No. Observations:              218800   AIC:                         2.913e+06
Df Residuals:                  218793   BIC:                         2.913e+06
Df Model:                           6                                         
Covariance Type:            nonrobust                                         
                                    coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------
Intercept     

# 3. QUESTION: How has the geographical distribution of tickets by route changed over four months, and what assumptions can be tested with external data?

<div style="background-color: #edede9; color: black; ">
    <h3 align="center"> </h3>
    <p style="font-size: 16px; text-align: justify; font-weight: 500; margin: 15px;">In this analysis, we want to see if flight ticket trends have changed geographically over the past four months. 
      We'll use the count of unique flights, with data from the previous section where we split multi-stop flights. 
      We’ll also use a metric: the ratio of flights on a selected route to the total flights <br>
      and analyze it daily across routes to check for changes.</p>
    <h3 align="center"> </h3>
</div>

In [9]:
q3 = unique_data[unique_data['flightDate'] < pd.to_datetime('2022-10-01')].copy()  
q3.loc[:, 'groupedDate'] = q3['flightDate'].dt.floor('5D') 
q3['path'] = q3['origin'] + '-' + q3['destination']
q3.head()

index origin destination  \
0  7a384f9b6a78a8ac3a5cd5444c8b2858    BOS         SEA   
1  7a384f9b6a78a8ac3a5cd5444c8b2858    SEA         SFO   
2  520332957f58509cb753e30c61ac9f2b    BOS         JFK   
3  520332957f58509cb753e30c61ac9f2b    JFK         SFO   
4  a288c560344067732f2ecd4e87eca7f3    BOS         JFK   

                  departure                        arrival flightDate  \
0 2022-06-03 23:05:00+00:00  2022-06-03T22:20:00.000-07:00 2022-06-03   
1 2022-06-04 13:00:00+00:00  2022-06-04T08:12:00.000-07:00 2022-06-04   
2 2022-06-03 10:05:00+00:00  2022-06-03T07:25:00.000-04:00 2022-06-03   
3 2022-06-03 13:30:00+00:00  2022-06-03T12:55:00.000-07:00 2022-06-03   
4 2022-06-03 13:40:00+00:00  2022-06-03T11:02:00.000-04:00 2022-06-03   

  groupedDate     path  
0  2022-06-02  BOS-SEA  
1  2022-06-02  SEA-SFO  
2  2022-06-02  BOS-JFK  
3  2022-06-02  JFK-SFO  
4  2022-06-02  BOS-JFK

### At this stage, we created many charts and examined them to understand the reasons for the changes. Here, we have drawn three sample charts using the defined metric

In [10]:
high_traffic_flight_paths = q3['path'].value_counts()[:3].keys()
path_flights_count = q3.groupby(['path', 'groupedDate']).size().to_frame('count').reset_index()
flights_count = q3.groupby(['groupedDate']).size().to_frame('total_count_of-day').reset_index()
path_flights_count = path_flights_count.merge(flights_count, how='left', on = 'groupedDate')
path_flights_count['ratio'] = path_flights_count['count'] / path_flights_count['total_count_of-day']
path_flights_count

for path in high_traffic_flight_paths:
    data = path_flights_count[path_flights_count['path'] == path][1:-1]
    fig1 = px.line(data, x='groupedDate', y='ratio',
                  title=path, markers=True, height = 400)
    
    fig1.update_traces(line=dict(color='#432818'))  
    fig1.update_layout(
        plot_bgcolor='#e9ecef',
        paper_bgcolor='white',
        title=dict(x=0.5))
    fig1.show()

### After looking at different routes and their possible causes, we found the following for the LAX to SJC route. We saw an increase in the numbers on June 24 and September 22. On June 25, a soccer match between LA Galaxy and San Jose Earthquakes was planned at a stadium 17 miles from San Jose International Airport. But the match was canceled the day before because of problems at the stadium. A new match was set for September 24, just before the next increase.
### We think the rise in ticket sales on these two dates was due to the soccer match.

In [11]:
data = path_flights_count[path_flights_count['path'] == 'LAX-SJC'][1:-1]
fig1 = px.line(data, x='groupedDate', y='ratio',
              title='LAX-SJC - ratio', markers=True, height = 400)
fig1.update_traces(line=dict(color='#432818'))  
fig1.update_layout(
    plot_bgcolor='#e9ecef',
    paper_bgcolor='white',
    title=dict(x=0.5))

fig1.show()

fig2 = px.line(data, x='groupedDate', y='count',
              title='LAX-SJC - number of flights', markers=True, height = 400)
fig2.update_traces(line=dict(color='#432818'))  
fig2.update_layout(
    plot_bgcolor='#e9ecef',
    paper_bgcolor='white',
    title=dict(x=0.5))

fig2.show()